# Assignment 3: Chicago Crimes

# MSDS420

# John Foxworthy

In [43]:
import folium
from folium import plugins
from folium.plugins import MarkerCluster
import psycopg2
import csv
import pandas as pd
import json
from area import area

from psycopg2.extensions import ISOLATION_LEVEL_AUTOCOMMIT 

In [44]:
# Use this data set for your final submission of your Assignment 3
# Uncomment the following line after you unit test your code and ready to run and submit your assignment on this dataset 

# db_connection = psycopg2.connect(host='129.105.248.26',dbname="chicago_crimes", user="YourNetID" , password="YourPassword")




# Use the following dataset for unit testing purposes only. It takes roughly 5 minutes to omplete.
# Comment the following line when you are done with your unit testing and ready to run your assignment on the complete dataset and submit your Assignment 

db_connection = psycopg2.connect(host='129.105.248.26',dbname="chicago_crimes_ut", user="jfi0932" , password="3ycNkbCjZH.gmXQrCRTw*LMK2gdcP_V")


cursor = db_connection.cursor()

In [45]:
# Get the column names for table crimes

cursor.execute("SELECT column_name FROM INFORMATION_SCHEMA.COLUMNS WHERE table_name = 'crimes';")

rows=cursor.fetchall()

rows

[('id',),
 ('caseno',),
 ('date_of_occurrence',),
 ('block',),
 ('iucr',),
 ('primary_type',),
 ('description',),
 ('location_description',),
 ('arrest',),
 ('domestic',),
 ('beat',),
 ('district',),
 ('ward',),
 ('community_area',),
 ('fbi_cd',),
 ('xcoordinate',),
 ('ycoordinate',),
 ('year',),
 ('updated_on',),
 ('latitude',),
 ('longitude',),
 ('location',),
 ('where_is',)]

In [46]:
# Get the column names for table police_stations

cursor.execute("SELECT column_name FROM INFORMATION_SCHEMA.COLUMNS WHERE table_name = 'police_stations';")

rows=cursor.fetchall()

rows

[('district',),
 ('district_name',),
 ('address',),
 ('city',),
 ('state',),
 ('zip',),
 ('website',),
 ('phone',),
 ('fax',),
 ('tty',),
 ('x_coordinate',),
 ('y_coordinate',),
 ('latitude',),
 ('longitude',),
 ('location',),
 ('where_is',)]

In [47]:
# Get 5 rows from the table crimes

cursor.execute("SELECT * from crimes limit 5;")

rows=cursor.fetchall()

rows

[(24368,
  'JC103046',
  datetime.datetime(2019, 1, 3, 14, 37),
  '050XX S INDIANA AVE',
  '110',
  'HOMICIDE',
  'FIRST DEGREE MURDER',
  'AUTO',
  False,
  False,
  224,
  2,
  3.0,
  '38',
  '01A',
  1178455.0,
  1871575.0,
  2019,
  datetime.datetime(2019, 1, 10, 15, 16),
  41.80290852,
  -87.62104831,
  '(41.802908524, -87.62104831)',
  '0101000020E6100000368AD5B4C5E64440E92B6941BFE755C0'),
 (24369,
  'JC103046',
  datetime.datetime(2019, 1, 3, 14, 37),
  '050XX S INDIANA AVE',
  '110',
  'HOMICIDE',
  'FIRST DEGREE MURDER',
  'AUTO',
  False,
  False,
  224,
  2,
  3.0,
  '38',
  '01A',
  1178455.0,
  1871575.0,
  2019,
  datetime.datetime(2019, 1, 10, 15, 16),
  41.80290852,
  -87.62104831,
  '(41.802908524, -87.62104831)',
  '0101000020E6100000368AD5B4C5E64440E92B6941BFE755C0'),
 (24370,
  'JC105864',
  datetime.datetime(2019, 1, 5, 16, 23),
  '012XX N ADA ST',
  '110',
  'HOMICIDE',
  'FIRST DEGREE MURDER',
  'STREET',
  False,
  False,
  1433,
  14,
  2.0,
  '24',
  '01A',
  

In [48]:
cursor.execute("SELECT count(*) from crimes;")

rows=cursor.fetchall()

rows

[(14436,)]

## Query #1:

In [49]:
cursor.execute("SELECT district, count(district) from crimes GROUP BY district")
rows=cursor.fetchall()

In [50]:
crimes_per_district = pd.DataFrame(rows, columns=['dist_num','number_of_crimes'])
crimes_per_district['dist_num'] = crimes_per_district['dist_num'].astype(str)

crimes_per_district.head()

dist_num  number_of_crimes
0       24               412
1       11              1113
2        8               886
3       19               608
4       25               726

In [51]:
crimes_dataset = pd.DataFrame(rows)

In [52]:
crimes_dataset.head()

0     1
0  24   412
1  11  1113
2   8   886
3  19   608
4  25   726

In [53]:
total_number_of_crimes_per_district_map = folium.Map(location =(41.8781, -87.6298),zoom_start=11)

In [54]:
folium.Choropleth(geo_data="Boundaries.geojson", 
              fill_color='OrRd', 
              fill_opacity=0.5, 
              line_opacity=1,
              data = crimes_per_district,
              key_on='feature.properties.dist_num',
              columns = ['dist_num', 'number_of_crimes']
              ).add_to(total_number_of_crimes_per_district_map)

In [55]:
cursor.execute("""SELECT ST_X(ST_AsText(Where_IS)), ST_Y(ST_AsText(Where_IS)), district from police_stations where district!='Headquarters'""")
police_stations = cursor.fetchall()

for police_station in police_stations:
    police_station_location = (police_station[0],police_station[1])
    cursor.execute("SELECT district, count(district) from crimes where district= %s GROUP BY district",[police_station[2]])
    districts_crime_numbers = cursor.fetchall()
    for district in districts_crime_numbers:
        folium.Marker(location = police_station_location,popup=folium.Popup(html="District No : %s  has   Total Number of Crimes:%s" %district ,max_width=450)).add_to(total_number_of_crimes_per_district_map)



### Lets plot the Choropleth map and notice the intensity of color on the different districts
### The Blue POPUP represents the location of police station in the different districts in the map

In [56]:
total_number_of_crimes_per_district_map

## Query #2:

In [57]:
violent_crime_categories='THEFT','ASSAULT','ROBBERY','KIDNAPPING','CRIM SEXUAL ASSAULT','BATTERY','MURDER'

In [58]:
cursor.execute("SELECT district, count(district) from crimes where PRIMARY_TYPE in %s GROUP BY district",[violent_crime_categories])
rows=cursor.fetchall()
violent_crime_data=pd.DataFrame(rows, columns=['district_num','number_of_violent_crimes'])
violent_crime_data['district_num'] = violent_crime_data['district_num'].astype(str)
violent_crime_data

district_num  number_of_violent_crimes
0             8                       488
1            11                       407
2            24                       216
3            19                       368
4            25                       362
5             4                       400
6            14                       309
7             3                       387
8            17                       220
9            20                       147
10           22                       217
11            9                       312
12            7                       367
13           10                       362
14            1                       624
15            5                       293
16           18                       605
17            2                       349
18           16                       252
19           15                       291
20            6                       457
21           12                       430

In [59]:
violent_crimes_per_district_map= folium.Map(location =(41.8781, -87.6298),zoom_start=11)
folium.Choropleth(geo_data="Boundaries.geojson", 
              fill_color='YlOrRd', 
              fill_opacity=0.5, 
              line_opacity=1,
              data = violent_crime_data,
              key_on='feature.properties.dist_num',
              columns = ['district_num', 'number_of_violent_crimes'],
              legend_name="VOILENT CRIME MAP"
              ).add_to(violent_crimes_per_district_map)

In [60]:
violent_crimes_per_district_map

## Query #3:

In [61]:
gun='%GUN%'
cursor.execute("SELECT district, count(district) from crimes where DESCRIPTION::text LIKE %s GROUP BY district",[gun])
districts_gun_violent_crimes = cursor.fetchall()
districts_gun_violent_crimes_df = pd.DataFrame(districts_gun_violent_crimes, columns=['dist_num','gun_crimes'])
districts_gun_violent_crimes_df['dist_num'] = districts_gun_violent_crimes_df['dist_num'].astype(str)
districts_gun_violent_crimes_df

dist_num  gun_crimes
0        24           9
1         8          49
2        11          69
3        19          11
4        25          43
5         4          50
6        14          12
7         3          57
8        17           7
9        20           5
10       22          24
11       10          58
12        9          39
13        7          67
14        1           6
15        5          44
16       18          14
17        2          34
18       16          12
19       15          34
20        6          63
21       12          38

In [62]:
districts_gun_violent_crimes_map = folium.Map(location =(41.8781, -87.6298),zoom_start=11)
folium.Choropleth(geo_data="Boundaries.geojson", 
              fill_color='YlOrRd', 
              fill_opacity=0.5, 
              line_opacity=1,
              data = districts_gun_violent_crimes_df,
              key_on='feature.properties.dist_num',
              columns = ['dist_num', 'gun_crimes'],
              legend_name="GUN CRIME"
              ).add_to(districts_gun_violent_crimes_map)

In [63]:

cursor.execute("""SELECT ST_X(ST_AsText(Where_IS)), ST_Y(ST_AsText(Where_IS)), district from police_stations where district!='Headquarters'""")

gun='%GUN%'
police_stations = cursor.fetchall()

for police_station in police_stations:
    police_station_location = (police_station[0],police_station[1])
    cursor.execute("""SELECT DESCRIPTION, count(DESCRIPTION) from crimes where district=%s and DESCRIPTION::text LIKE %s GROUP BY DESCRIPTION""",[police_station[2],gun])
    district_gun_violent_crimes=cursor.fetchall()
    district_gun_violent_crimes_df=pd.DataFrame(district_gun_violent_crimes, columns=['Description', 'Number of Gun Crime'])
    header = district_gun_violent_crimes_df.to_html(classes='table table-striped table-hover table-condensed table-responsive')
    folium.Marker(location=police_station_location,popup=folium.Popup(html="District No: %s GUN_Crime: %s" %(police_station[2],header) )).add_to(districts_gun_violent_crimes_map)
    

In [64]:
districts_gun_violent_crimes_map

## Query #4:

In [65]:
district=[]
tarea=[]

with open('Boundaries.geojson') as f:
    data = json.load(f)
    a = data['features']
    for i in range(len(a)):
        obj=a[i]['geometry']
        n= a[i]['properties']
        district.append(n['dist_num'])
        tarea.append(area(obj)/10000)

af=pd.DataFrame({'dist_num': district,'district_area_inHectares':tarea})
af['dist_num'] = af['dist_num'].astype(str)
final_data= pd.merge(af, crimes_per_district, on='dist_num', how='inner')
final_data['crime_density'] = round(final_data['number_of_crimes']/(final_data['district_area_inHectares']/100))
final_data

dist_num  district_area_inHectares  number_of_crimes  crime_density
0        17               2492.727155               386           15.0
1        20               1132.170216               254           22.0
2        19               2225.035732               608           27.0
3        25               2827.989237               726           26.0
4        14               1555.869965               508           33.0
5         7               1688.670732               745           44.0
6         3               1576.063931               695           44.0
7         4               7068.152865               790           11.0
8         6               2099.682124               844           40.0
9        22               3490.416073               442           13.0
10        5               3318.613379               635           19.0
11       24               1406.081387               412           29.0
12       16               8171.776367               473            6.0
13        8               5992.169760               886           15.0
14       18               1215.520046               869           71.0
15       12               2509.453028               700           28.0
16       11               1582.727274              1113           70.0
17       15                989.631393               530           54.0
18       10               2038.988883               779           38.0
19        1               1214.818895               854           70.0
20        9               3505.216898               585           17.0
21        2               1949.690970               602           31.0

## Query #5:

In [66]:
gun_crime_arrests_map = folium.Map(location =(41.8781, -87.6298),zoom_start=11)
folium.Choropleth(geo_data="Boundaries.geojson", 
              fill_color='YlOrRd', 
              fill_opacity=0.5, 
              line_opacity=1,
              data = districts_gun_violent_crimes_df,
              key_on='feature.properties.dist_num',
              columns = ['dist_num', 'gun_crimes'],
              legend_name="GUN CRIME"
              ).add_to(gun_crime_arrests_map)

In [67]:
cursor.execute("""SELECT ST_X(ST_AsText(Where_IS)), ST_Y(ST_AsText(Where_IS)), district from police_stations where district!='Headquarters'""")
gun='%GUN%'

police_stations = cursor.fetchall()

marker_cluster = MarkerCluster().add_to(gun_crime_arrests_map)

for police_station in police_stations:
    police_station_location = (police_station[0],police_station[1])
    cursor.execute("""SELECT DISTINCT ON(caseno) caseno, block,DESCRIPTION, count(arrest), arrest,latitude, longitude from crimes where district=%s and DESCRIPTION::text LIKE %s GROUP BY caseno,block, DESCRIPTION,arrest, latitude, longitude""",[police_station[2],gun])
    crimes_per_district = cursor.fetchall()
    for crime in crimes_per_district:
        if crime[4]==True:
            folium.Marker(location=(crime[5],crime[6]),popup=folium.Popup(html="District No: %s <br> Description: %s <br> Block: %s" %(police_station[2],crime[2],crime[1])),icon=folium.Icon(color='green', icon='ok-sign'),).add_to(marker_cluster)
        else:
            folium.Marker(location=(crime[5],crime[6]),popup=folium.Popup(html="District No: %s <br> Description: %s<br> Block: %s" %(police_station[2],crime[2],crime[1])),icon=folium.Icon(color='red', icon='remove-sign'),).add_to(marker_cluster)          



In [68]:
crimes_per_district[:3]

[('JC100027',
  '017XX N MAYFIELD AVE',
  'UNLAWFUL POSS OF HANDGUN',
  1,
  True,
  41.91205157,
  -87.7728073),
 ('JC100191',
  '017XX N NEWCASTLE AVE',
  'UNLAWFUL POSS OF HANDGUN',
  1,
  True,
  41.91174566,
  -87.7960732),
 ('JC103615',
  '019XX N LA CROSSE AVE',
  'ARMED: HANDGUN',
  1,
  False,
  41.91638097,
  -87.74732207)]

In [69]:
gun_crime_arrests_map

## Query #6:

In [70]:
farthest_block_gun_crime_map = folium.Map(location =(41.8781, -87.6298),zoom_start=11)
folium.Choropleth(geo_data="Boundaries.geojson", 
              fill_color='YlOrRd', 
              fill_opacity=0.5, 
              line_opacity=1,
              data = districts_gun_violent_crimes_df,
              key_on='feature.properties.dist_num',
              columns = ['dist_num', 'gun_crimes'],
              legend_name="GUN CRIME"
             ).add_to(farthest_block_gun_crime_map)

In [71]:
cursor.execute("""SELECT ST_X(ST_AsText(Where_IS)), ST_Y(ST_AsText(Where_IS)), 
district from police_stations where district!='Headquarters'""")
police_stations = cursor.fetchall()

gun='%GUN%'

for police_station in police_stations:
    
    cursor.execute("""
                        WITH crime_distance_from_police_station AS (
                                        SELECT  A.where_is as crime_where_is, 
                                                B.where_is as police_where_is,
                                                A.district as crime_district,
                                                A.block as crime_block,
                                                ST_Distance(A.where_is,B.where_is) as distance 
                                        FROM crimes as A, police_stations as B 
                                        WHERE A.district=%s and DESCRIPTION::text LIKE %s and B.district= %s 
                        )
    
                        SELECT DISTINCT on (crime_distance_from_police_station.crime_block) 
                                        crime_distance_from_police_station.crime_district,
                                        crime_distance_from_police_station.crime_block, 
                                        crime_distance_from_police_station.crime_where_is,
                                        crime_distance_from_police_station.distance 
                        FROM crime_distance_from_police_station 
                        WHERE distance = (SELECT max(distance) 
                                        FROM crime_distance_from_police_station )""",[police_station[2],gun,police_station[2]])
    
    farthest_block_gun_crime = cursor.fetchall()

    cursor.execute("SELECT ST_X(ST_AsText(%s)), ST_Y(ST_AsText(%s))",(farthest_block_gun_crime[0][2],
                                                                      farthest_block_gun_crime[0][2]))
    farthest_block_gun_crime_location = cursor.fetchall()
    folium.Marker(location=(police_station[0],police_station[1]),
                  popup=folium.Popup(html="Police Station <br> District No.:%s <br> Farthest Gun_Crime Block:%s"%(farthest_block_gun_crime[0][0],
                                                                                                                  farthest_block_gun_crime[0][1]))).add_to(farthest_block_gun_crime_map)
    folium.CircleMarker(farthest_block_gun_crime_location[0],radius=5,color='#ff3187',
                        popup=folium.Popup(html="District No.:%s <br> Block:%s"%(farthest_block_gun_crime[0][0],
                                                                                 farthest_block_gun_crime[0][1]))).add_to(farthest_block_gun_crime_map) 

In [72]:
farthest_block_gun_crime_map

### Requirements

#### The PDF document your are submitting must have the source code and the output for the following requirements

#### Requirement #1:

#### Calculate the gun crimes density in every district

In [77]:
gun_crime_density = pd.merge(af, districts_gun_violent_crimes_df, on='dist_num', how='inner')
gun_crime_density['crime|_density'] = round(gun_crime_density['gun_crimes']/(final_data['district_area_inHectares']/100))
gun_crime_density

dist_num  district_area_inHectares  gun_crimes  crime|_density
0        17               2492.727155           7             0.0
1        20               1132.170216           5             0.0
2        19               2225.035732          11             0.0
3        25               2827.989237          43             2.0
4        14               1555.869965          12             1.0
5         7               1688.670732          67             4.0
6         3               1576.063931          57             4.0
7         4               7068.152865          50             1.0
8         6               2099.682124          63             3.0
9        22               3490.416073          24             1.0
10        5               3318.613379          44             1.0
11       24               1406.081387           9             1.0
12       16               8171.776367          12             0.0
13        8               5992.169760          49             1.0
14       18               1215.520046          14             1.0
15       12               2509.453028          38             2.0
16       11               1582.727274          69             4.0
17       15                989.631393          34             3.0
18       10               2038.988883          58             3.0
19        1               1214.818895           6             0.0
20        9               3505.216898          39             1.0
21        2               1949.690970          34             2.0

### Requirement #2:

#### Locate the farthest UNLAWFUL POSS OF HANDGUN crime from the police station in every district. The popup on Choropleth map shall display the district number and the block

In [80]:
cursor.execute('SELECT * FROM get_gun_crimes(\'{}\');'.format('UNLAWFUL POSS OF HANDGUN'))

handgun_crimes_df = pd.DataFrame(cursor.fetchall(), columns = ['District', 'Block', 'BlockCrimes', 'DistrictCrimes', 'X_Coord', 'Y_Coord'])

InFailedSqlTransaction: current transaction is aborted, commands ignored until end of transaction block


In [79]:
handgun_crimes_df.head()

NameError: name 'handgun_crimes_df' is not defined

In [81]:
handgun_crimes_map = folium.Map(location =(41.8781, -87.6298),zoom_start=11)

handgun_crimes_map.choropleth(
    geo_data="Boundaries.geojson", 
    fill_color='YlOrRd', 
    fill_opacity=0.5, 
    line_opacity=1,
    data = handgun_crimes_by_district_df,
    key_on='feature.properties.dist_num',
    columns = ['district', 'handgun_crimes'],
    legend_name="HANDGUN CRIME")

NameError: name 'handgun_crimes_by_district_df' is not defined

In [83]:
cursor.execute('SELECT * FROM get_furthest_crimes(\'{}\');'.format('UNLAWFUL POSS OF HANDGUN'))

furthest_handgun_crimes_df = pd.DataFrame(cursor.fetchall(), columns = ['district', 'Block', 'DistrictCrimes', 'Station_X_Coord', 'Station_Y_Coord', 'Crime_X_Coord', 'Crime_Y_Coord'])

InFailedSqlTransaction: current transaction is aborted, commands ignored until end of transaction block


### Requirement #3:

#### Create Marker Clusters on Choropleth map for those gun related violent crimes that have Location Desciption as RESIDENCE in ** (green icon)** and those that have Location Desciption as STREET in (red icon)

In [84]:
cursor.execute('SELECT * FROM get_gun_crimes(\'{}\');'.format('GUN'))

gun_violent_crimes_df = pd.DataFrame(cursor.fetchall(), columns = ['District', 'Block', 'BlockCrimes', 'DistrictCrimes', 'X_Coord', 'Y_Coord'])

InFailedSqlTransaction: current transaction is aborted, commands ignored until end of transaction block


In [85]:
gun_violent_crimes_df = gun_crimes_df.groupby('District')['DistrictCrimes'].max().reset_index()
gun_violent_crimes_df.columns = ['district', 'handgun_crimes']
gun_violent_crimes_df.district = gun_crimes_by_district_df.district.apply(str)

NameError: name 'gun_crimes_df' is not defined

In [86]:
gun_cluster_map = folium.Map(location =(41.8781, -87.6298),zoom_start=11)

gun_cluster_map.choropleth(
    geo_data="Boundaries.geojson", 
    fill_color='YlOrRd', 
    fill_opacity=0.5, 
    line_opacity=1,
    data = gun_violent_crimes_df,
    key_on='feature.properties.dist_num',
    columns = ['district', 'handgun_crimes'],
    legend_name="HANDGUN CRIME")

NameError: name 'gun_violent_crimes_df' is not defined

### Requirement #4:

#### Locate the Block that has the higest number of gun crimes. The popup on Choropleth map shall display the Block in every district along with the total number of gun crimes for that block

In [87]:
cursor.execute('SELECT * FROM get_gun_crimes(\'{}\');'.format('GUN'))

gun_crimes_df = pd.DataFrame(cursor.fetchall(), columns = ['District', 'Block', 'BlockCrimes', 'DistrictCrimes', 'X_Coord', 'Y_Coord'])

InFailedSqlTransaction: current transaction is aborted, commands ignored until end of transaction block


In [88]:
cursor.execute('SELECT * FROM get_gun_crimes(\'{}\');'.format('GUN'))

gun_crimes_df = pd.DataFrame(cursor.fetchall(), columns = ['District', 'Block', 'BlockCrimes', 'DistrictCrimes', 'X_Coord', 'Y_Coord'])

InFailedSqlTransaction: current transaction is aborted, commands ignored until end of transaction block


In [89]:
gun_crimes_by_district_df = gun_crimes_df.groupby('District')['DistrictCrimes'].max().reset_index()
gun_crimes_by_district_df.columns = ['district', 'gun_crimes']
gun_crimes_by_district_df.district = gun_crimes_by_district_df.district.apply(str)

NameError: name 'gun_crimes_df' is not defined

In [90]:
most_gun_crimes_map = folium.Map(location =(41.8781, -87.6298),zoom_start=11)

most_gun_crimes_map.choropleth(
    geo_data="Boundaries.geojson", 
    fill_color='YlOrRd', 
    fill_opacity=0.5, 
    line_opacity=1,
    data = gun_crimes_by_district_df,
    key_on='feature.properties.dist_num',
    columns = ['district', 'gun_crimes'],
    legend_name="GUN CRIME")

NameError: name 'gun_crimes_by_district_df' is not defined

In [91]:
districts = gun_crimes_df.District.unique()

district_crimes = {}

for district in districts:
    district_df = gun_crimes_df[ gun_crimes_df['District'] == district ]
    district_crimes[ district] = [ district_df.Block.unique(), district_df.iloc[0].BlockCrimes,
                              district_df.iloc[0].X_Coord, district_df.iloc[0].Y_Coord]

NameError: name 'gun_crimes_df' is not defined

In [92]:
for d in district_crimes:
    blocks = district_crimes[d][0]
    crimes = district_crimes[d][1]
    folium.Marker(location = [district_crimes[d][2], district_crimes[d][3]], 
                  popup = folium.Popup(html= "District {} had {} block(s) \[ ({}) \] with {} crimes.".format( d, len(blocks), ', '.join(blocks), crimes), 
                    max_width=450)).add_to(most_gun_crimes_map)

NameError: name 'district_crimes' is not defined

In [93]:
most_gun_crimes_map